In [6]:
# Discretize the country using the original minimalist_coning.geojson

import geopandas as gpd
from shapely.geometry import box
import numpy as np
import folium

# Load minimalist_coning.geojson
slovenia = gpd.read_file("maps/minimalist_coning.geojson")

slovenia = slovenia.to_crs(epsg=3857)

# Get bounds of Slovenia based on 
minx, miny, maxx, maxy = slovenia.total_bounds

# Set bin size in meters
bin_size = 5_000

# Create grid cells
x_coords = np.arange(minx, maxx, bin_size)
y_coords = np.arange(miny, maxy, bin_size)

polygons = [box(x, y, x + bin_size, y + bin_size) for x in x_coords for y in y_coords]
grid = gpd.GeoDataFrame(geometry=polygons, crs=slovenia.crs)

# Clip to Slovenia boundary and go back to lat and lon measures
grid_selected = gpd.sjoin(grid, slovenia, how='inner', predicate='intersects')
grid_selected = grid_selected.to_crs(epsg=4326)
grid_selected = grid_selected.drop(columns=['index_right'])
grid_selected["ID"] = range(len(grid_selected))

In [7]:
display(grid_selected)
grid_selected.to_file("maps/zoning.geojson", driver="GeoJSON")

m= folium.Map(location=[46, 14])
folium.GeoJson(
    grid_selected,
).add_to(m)
m

geometry    ID
25    POLYGON ((13.41992 46.2044, 13.41992 46.23548,...     0
26    POLYGON ((13.41992 46.23548, 13.41992 46.26654...     1
27    POLYGON ((13.41992 46.26654, 13.41992 46.29758...     2
27    POLYGON ((13.41992 46.26654, 13.41992 46.29758...     3
28    POLYGON ((13.41992 46.29758, 13.41992 46.3286,...     4
...                                                 ...   ...
3325  POLYGON ((16.56402 46.51438, 16.56402 46.54528...  9509
3326  POLYGON ((16.56402 46.54528, 16.56402 46.57616...  9510
3370  POLYGON ((16.60894 46.45253, 16.60894 46.48346...  9511
3371  POLYGON ((16.60894 46.48346, 16.60894 46.51438...  9512
3417  POLYGON ((16.65385 46.45253, 16.65385 46.48346...  9513

[9514 rows x 2 columns]